In [1]:
import csv
import os
from emoji import UNICODE_EMOJI
import nltk
emoji_set = set(UNICODE_EMOJI)

In [27]:
def process_text(text):
    text = text.replace("RT ", "")
    text = text.replace("\n", " ")
    words = text.split(" ")

    for word in words:
        if word.startswith("@") or word.startswith("http"):
            text = text.replace(word, "")
    
    return text.strip()

In [22]:
def get_emojis_in_text(text, emoji_set):
    char_set = set(text)
    print(char_set)
    all_emojis = emoji_set & char_set
    
    return all_emojis

In [4]:
def clean_text(tweet):
    cleaned_str = tweet['processed_text']
    for emoji in tweet['emojis_in_text']:
        cleaned_str = tweet['processed_text'].replace(emoji, "")
        
    return cleaned_str

In [5]:
tweets = []
with open('twitter_october.csv', 'r') as csv_file:
    print("reading csv...")
    csv_reader = csv.DictReader(csv_file)
    print("done")
    print("processing text")
    count = 0
    for row in csv_reader:
        if row['text'] == 'text':
            continue
        row['processed_text'] = process_text(row['text'])
        row['emojis_in_text'] = get_emojis_in_text(row['processed_text'], emoji_set)
        tweets.append(row)
        count += 1
        if count % 500000 == 0:
            print("processed", count, "tweets")

reading csv...
done
processing text
processed 500000 tweets
processed 1000000 tweets
processed 1500000 tweets
processed 2000000 tweets
processed 2500000 tweets
processed 3000000 tweets
processed 3500000 tweets
processed 4000000 tweets
processed 4500000 tweets
processed 5000000 tweets


In [7]:
len(tweets)

5169003

In [8]:
tweets[117]

OrderedDict([('created_at', 'Thu Oct 18 16:24:00 +0000 2018'),
             ('id', '1052958485652992000'),
             ('id_str', '1052958485652992000'),
             ('text',
              'RT @ardenturges: These slippery iridescent VS bikini panties are one of my favs, as you can probably tell 😳\n#foilpanties #fetish #kink http…'),
             ('in_reply_to_status_id', ''),
             ('user_id', '988766328'),
             ('user_id_str', '988766328'),
             ('user_screen_name', 'int_femenino'),
             ('processed_text',
              'These slippery iridescent VS bikini panties are one of my favs, as you can probably tell 😳\n#foilpanties #fetish #kink'),
             ('emojis_in_text', {'😳'})])

In [9]:
class Indexer(object):
    """
    Bijection between objects and integers starting at 0. Useful for mapping
    labels, features, etc. into coordinates of a vector space.

    Attributes:
        objs_to_ints
        ints_to_objs
    """
    def __init__(self):
        self.objs_to_ints = {}
        self.ints_to_objs = {}

    def __repr__(self):
        return str([str(self.get_object(i)) for i in range(0, len(self))])

    def __str__(self):
        return self.__repr__()

    def __len__(self):
        return len(self.objs_to_ints)

    def get_object(self, index):
        """
        :param index: integer index to look up
        :return: Returns the object corresponding to the particular index or None if not found
        """
        if (index not in self.ints_to_objs):
            return None
        else:
            return self.ints_to_objs[index]

    def contains(self, object):
        """
        :param object: object to look up
        :return: Returns True if it is in the Indexer, False otherwise
        """
        return self.index_of(object) != -1

    def index_of(self, object):
        """
        :param object: object to look up
        :return: Returns -1 if the object isn't present, index otherwise
        """
        if (object not in self.objs_to_ints):
            return -1
        else:
            return self.objs_to_ints[object]

    def add_and_get_index(self, object, add=True):
        """
        Adds the object to the index if it isn't present, always returns a nonnegative index
        :param object: object to look up or add
        :param add: True by default, False if we shouldn't add the object. If False, equivalent to index_of.
        :return: The index of the object
        """
        if not add:
            return self.index_of(object)
        if (object not in self.objs_to_ints):
            new_idx = len(self.objs_to_ints)
            self.objs_to_ints[object] = new_idx
            self.ints_to_objs[new_idx] = object
        return self.objs_to_ints[object]

In [17]:
from collections import Counter

def get_labels(tweet, indexer):
    
    all_emojis = tweet['emojis_in_text']
    emojis = {}
    c = Counter()
    for emoji in all_emojis:
        indexer.add_and_get_index(emoji)
        c[emoji] += tweet['processed_text'].count(emoji)
    
    print(all_emojis)
    #print("txt", tweet['processed_text'])
    max_score = max(c.values())
    labels = [indexer.index_of(k) for k in c if c[k] == max_score]
    
    return labels
                    
                    
                
        

        

In [29]:
class DataPoint():
    def __init__(self, text, label):
        self.text = text
        self.label = label

In [30]:
def create_dataset(tweets, indexer):
    dataset = []
    for idx, tweet in enumerate(tweets):
        #print(idx, tweet['processed_text'])
        try:
            labels = get_labels(tweet, indexer)
        except:
            continue
        cleaned_text = clean_text(tweet)
        for label in labels:
            datapoint = DataPoint(cleaned_text, label)
            dataset.append(datapoint)
            
    return dataset

In [ ]:
indexer = Indexer()
dataset = create_dataset(tweets, indexer)

0 Said Michael was from Texas 😂😂
{'😂'}
1 United vibe 👏🏽👏🏽👏🏽 they so cuteee awwww #XFactor
{'👏'}
2 Happy 47th Birthday to Snoop Dogg 💙
{'💙'}
3 TRUE FACTS 💯
{'💯'}
4 THANK YOU BTS. I NEVER WOULD HAVE MET EMERALD IF IT WERENT FOR YOU 💞
{'💞'}
5 Free Me 🖤 Be Home Real Soon.
{'🖤'}
6 What did y'all call this back then in school?

Me: fraps😂
{'😂'}
7 Free Me 🖤 Be Home Real Soon.
{'🖤'}
8 When you fall for someone, everything about them becomes beautiful. 😍
{'😍'}
9 We play like the Liverpool of a few years ago tbh. No wonder Suarez and Coutinho feel so comfortable 😑
{'😑'}
10 Switching it up tonite 😈
{'😈'}
11 Love this family hehee💓

#차키
{'💓'}
12 A&amp;P is hard but we try our best 😇
{'😇'}
13 Personalize Yours🔥💕   #etsy#etsymntt #etsy #ebay #etsyretwt #epiconetsy #etsyaaa #bride…
{'💕', '🔥'}
14 Why be mad if he keeping it 💯
{'💯'}
15 I hug u 🤗
I embrace u
I protect u ⚔
{'🤗', '⚔'}
16 Appreciate ya😎🤙🏾💯
{'💯', '🤙', '😎'}
17 I don’t see any boyfriends getting love for Sweetest Day. It’s rough out here 😂
{'

440 The man who won the women's cycling competition is now calling the woman transphobic. Lol 🤔
{'🤔'}
441 [INSTAGRAM CAROUSEL] taeyeon_ss: 🕷  (5P) #taengstagram
{'🕷'}
442 Crab broke my corgi 😅
{'😅'}
443 That smile 😭 an angel indeed  #BTS #BTSinBerlin #BTSinBerlinD2 #JIMIN
{'😭'}
444 Really pleased you enjoyed☺️
{'☺'}
445 181016 LYS IN BERLIN
ending 😂😂
SUGA now SUG since he lost his ring 🤦‍♀️
@BTS_twt 
#SUGA #SUG #슈가 #방탄소년단 #BTS
{'🤦', '😂', '♀'}
446 Win!
A Batwoman Funko Pop 🦇 
To enter....
👉Follow  #DCWORLDBATWOMAN 
👉Re-Tweet this post 
One winner announci…
{'🦇', '👉'}
447 ‼️‼️
I don’t get WHY people are so mean. The same thing happened to me and I explained how I got my tickets WHEN TH…
{'‼'}
448 UPCOMING SCHEDULE | 181225

2018 SBS Gayo Daejeon [End of year show]

🗓 25th December
📌 Seoul Gocheok Dome

✍🏻 Appearanc…
{'🗓', '📌', '✍'}
449 “mxdric” 🤣
{'🤣'}
450 Baecation ❤️🌴
{'🌴', '❤'}
451 181018 Leeteuk Shindong at O shopping studio ♥️💕💕#SJxOshoppingRound2
{'💕', '♥'}
452 1017 LYS IN BERLIN 🇩

{'‼', '🌴', '🎬'}
961 rt to be in LEENIS™️
- ITS AN IMESSAGE GC
- don’t be soft we do hazing
- all love and peace and positivity 
- we kinda f…
{'™'}
962 Wow wonyoung looks really good in the center position. She stood out the most for me👌👌
{'👌'}
963 Back to the old me 🤷🏽‍♀️
{'♀', '🤷'}
964 YES WE DID 💕🌷☀️
{'🌷', '💕', '☀'}
965 now whenever i listen to “party favor” i think of  and i’m not upset 🖤
{'🖤'}
966 Pray, forgive your self, appriciate others efforts, do things you enjoy , remaind your self that are loved. 😊
{'😊'}
967 I AM FUCKING SCREAMING 😂😂😂😂😂😂
{'😂'}
968 I love that bootyy😍😍
{'😍'}
969 I’m Getting Too Old For 3 Am Booty Calls, If You Ain’t Tryna Fuck By 10:30.. I’m Going To Bed 😂😂
{'😂'}
970 A boy asked his father the meaning of politics. Watch till the end.😂😂😂
{'😂'}
971 🕊️Prayer Train
Lets Pray Today for
🔺Justice Kavanaugh
🔺President Donald J Trump
🔺America
Today is the day the "Witches" ch…
{'🕊', '🔺'}
972 Girls who have these thunderstorms please quote this tweet and follow me I'l

1453 How do you meditate in the morning without falling asleep? 😂
{'😂'}
1454 How do you meditate in the morning without falling asleep? 😂
{'😂'}
1455 Fern.  at #PinoyPlaylist2018 

LISTEN to his songs on  ➡️
{'➡'}
1456 Nothing better than sleeping with the person u love everyday💛💛
{'💛'}
1457 do it pussy💞💞
{'💞'}
1458 Tag someone you love💓💕💖
{'💓', '💕', '💖'}
1459 Focused. 👊 

#HUDLIV
{'👊'}
1460 They said that this was their year and now we have Hope World and Mono...💜
#RM2isComing
{'💜'}
1461 I've not played it solo but also I think you need something stronger than pistol 😑
{'😑'}
1462 Long story 🤦🏾‍♀️ if i say it again ima just get mad all over again😂
{'🤦', '😂', '♀'}
1463 About fucking time 🙌🏻
{'🙌'}
1464 Sakura's picture really snapped. You can bash me but I think Sakura's official teaser photo is the best! ❤

Ps. I'm not d…
{'❤'}
1465 Thinking of you 💓
{'💓'}
1466 omg adidas used papillon as bgm for their fashion show!!!! they love jackson 😂 (cr teamwang-想想挺旺)
{'😂'}
1467 God blessed me 🙏🏾 a

{'🙈', '😍'}
1914 My thoughts and prayers are with all those involved in the helicopter accident at Leicester City. 🙏🏻
{'🙏'}
1915 Im just tired!!! 🤦🏽‍♀️🤦🏽‍♀️🤦🏽‍♀️
{'🤦', '♀'}
1916 Bro stop asking me to vote I’m a felon 😂
{'😂'}
1917 #CatsofTwitter 😻 🙏Follow/@AlfieMissing 
A COMPLETELY BLACK 😺, He is #MISSING from #Richmond area #Yorkshire DL10 😖
He was…
{'🙏', '😺', '😻', '😖'}
1918 LilDrew X Alize - 2 Birds 1 Stone 

OUT NOW ON SOUNDCLOUD‼️

LINK IN BIO 💪🏼💙
{'💙', '‼', '💪'}
1919 Same for me 😒
{'😒'}
1920 If I’m delusional about nigga that nigga delusional about me too😌 &amp; it’s my nigga at that🤷🏽‍♀️
{'😌', '♀', '🤷'}
1921 Atleti Forever 💪🏻😎
{'😎', '💪'}
1922 Amen. A prayer from the heart ❤️
{'❤'}
1923 Preach,  🗣
{'🗣'}
1924 An ode to a classic 💋
{'💋'}
1925 It's. For. Americans.
A. Mer. Ri. Cans.

FFS 🎃🙈
{'🙈', '🎃'}
1926 New Admin or ? 😂🔥
{'🔥', '😂'}
1927 can luke hemmings stop paying me dust 🤠
{'🤠'}
1928 Why is it that the states that require an ID to vote tend to never elect Democrats?

🤔
{'🤔'}
192

...

86822 Papichulo since day 1 though 😍
{'😍'}
86823 Yixing said he also wants a whale....so they adopted one for him 😂 Nothing can stop Xingmis 🤣
#LayZhang 
#LayGiveMeAChance
#Gi…
{'🤣', '😂'}
86824 If it's afternoon in your country, retweet this 💙

#PCAs #TheGroup #SuperJunior
@SJofficial
{'💙'}
86825 According to   immediate impact should have surprised no one.

 📝🎥
{'📝', '🎥'}
86826 HIT YOU WITH THAT 400 MILLION VIEWS!✨💗
@ygofficialblink 

Again, challenged myself to make a poster made out of screenshots f…
{'💗', '✨'}
86827 Ermagod BT21 soft mini pillow cushions 😍☁️
Look at their little tushies 
#PCAs #TheSong #IDOL
{'☁', '😍'}
86828 🏆 ASIA ARTIST AWARDS 🏆

⏰ Oct 6 - 11:00 AM KST 

Rank

1. BTS   : 4,095,850 (13.8%)
2. E       : 3,819,379 (12.9%)

Gap:…
{'⏰', '🏆'}
86829 If I say “I’m not gone tell nobody” my boyfriend doesn’t count 🤣
{'🤣'}
86830 New stream schedule coming november!🎥 I will be getting new work hours. I will no longer be a night shift worker so…
{'🎥'}
86831 Every single perso

87287 🏆 IDOL CHAMP 🏆

❗️1 DAY LEFT ❗️

⏰ Oct 30 - 12:20 AM KST

ARMYs join us again for another mass voting tomorrow 10:30PM K…
{'⏰', '🏆', '❗'}
87288 👸 Sunday is the best day for lingerie (65 Photos)
{'👸'}
87289 5 Time Champion Club! #F1🏎
{'🏎'}
87290 I genuinely hope that one day (hopefully in the near future 😭) I can forgive myself for all the mistakes I've made thi…
{'😭'}
87291 anyways who am i to judge...that song kinda goes off 😳
{'😳'}
87292 RIP to all the fallen soldiers 🙏
Rip Mac Miller
Rip xxxtentacion 
Rip Lil Peep
Rip Speaker Knockerz
Rip Lil Snupe
Rip Dex Osa…
{'🙏'}
87293 Who you gonna call?  🚫👻 

34 years ago this year 'Ghostbusters’ was first released. Retweet if you agree it’s an 80s class…
{'👻', '🚫'}
87294 Ooohhh new jp bandori event looks like its a drama club one which means more Kaoru/Maya interactions 👌
{'👌'}
87295 Im SINGLE Single..Extra Single..Heavy Onna Single...Wit A Lil Single Onna Side🤣😩....
{'🤣', '😩'}
87296 #NowPlaying: The Ultimate Playlist For The Ultimate i

87672 🖥 The computer processing power is applied in any domain that uses image or video rendering. How about making that power avail…
{'🖥'}
87673 What a season 👏

#JapaneseGP
{'👏'}
87674 Gets me everytime😂
{'😂'}
87675 What a season 👏

#JapaneseGP
{'👏'}
87676 That fight was brewing for years 👀
{'👀'}
87677 That's a lot, a lot of T-shirt 🙌
{'🙌'}
87678 People swear they down for you 😂 bitch i just need the key to the house
{'😂'}
87679 Retweeting to help some harried parent whose kid doesn’t know what to do for their science project. 😳
{'😳'}
87680 runs in the name😜
{'😜'}
87681 The Miami fans give  a standing ovation as enters the game for the first time in his final home opener! 👏

#HEATCultu…
{'👏'}
87682 avatar aang be like:

          🔷🔷🔷
          🔷🔷🔷
     🔷🔷🔷🔷🔷     
        🔷🔷🔷🔷
          🔷🔷🔷    
             🔷🔷…
{'🔷'}
87683 Follow everyone who retweets &amp; likes this💫
{'💫'}
87684 Roll Like A. Queen..........👑💙 Snatch That Jaw Line! #yassssssqueens #beautyroller #mdnaskin #visionaaron

88105 I'm a failure 😔
{'😔'}
88106 “knot” 💀💀💀
{'💀'}
88107 Bellandur foam lake 😍😍👇🏼👇🏼👇🏼 #Bengaluru
{'😍', '👇'}
88108 I snap one person and I’m surprised I have a “streak” 😂
{'😂'}
88109 #MAYWARDForAdvancePaper is second spot nationwide! Congratulations,  &amp;  ✨
{'✨'}
88110 Wooohooo!!!💕 Heartiest congratulations  to   and their families on the arrival of their…
{'💕'}
88111 latinas only care about zodiac signs because we grew up watching 12 corazones 😂😂
{'😂'}
88112 This photographer who was approached by a baby deer and a baby wolf

📷: Liba Radova
{'📷'}
88113 Abeg somebody should forward this to my dad😂😂😂
{'😂'}
88114 Only BTS can outsold themselves. That is legendary behaviour 👑 

Congratulations #BTS and ARMYs! 🎉

#RMonoBB200
{'🎉', '👑'}
88115 thank you, good luck!! 💯
{'💯'}
88116 A closeup of the bbs bc u deserve it ❤️ 

@whydontwemusic 
#iHeartWhyDontWe
https://t.co/Ww2sKUe5cm
{'❤'}
88117 They tryna see us down free my brotha.🔓
{'🔓'}
88118 IF YOU NEED A NEW BADA$$ ALBUM IN YOUR LIFE ‼️
{'

{'⭐', '🥂'}
88689 sometimes just hearing your voice is all i need❤️
{'❤'}
88690 Romelu Lukaku with the stepovers...

[🎥: U.S. only]
{'🎥'}
88691 Just wanna give a s/o to God right quick , the man been showing out fr fr 😩
{'😩'}
88692 📸 Alicia Vikander at the #LVSS19 show in Paris tonight. #AliciaVikander
{'📸'}
88693 Lol girl! I can’t make it without my nap. 😂
{'😂'}
88694 explore your boundaries 🌀
{'🌀'}
88695 that fucking macaroni and cheese looks like it’s to die for 😶
{'😶'}
88696 💃🏾💃🏾💃🏾yasss. thanx babe
{'💃'}
88697 Let's settle this once and for all.
Like for Manuel car ❤
Retweet for automatic 🔁
{'🔁', '❤'}
88698 Let's Gain followers real fast.

❣️ Retweet this tweet
❣️ Follow all Retweets
❣️ Follow me

❣️Kindly follow back❣️

Turn on m…
{'❣'}
88699 Thank you for blessing me with that conversation young king 🙏🏾
{'🙏'}
88700 Jest my edit 😉 After Starting The Sarkar Audio Launch The Lights Will be Ridham in Hall 😎🔥
#ThalapathyVijay Anna Entry 🔥…
{'😉', '🔥', '😎'}
88701 €  😎Follow everyone who 